# The DaCHS Prototype for Persistent TAP Uploads

From its beginning, TAP has let users upload their tables; but these uploads only existed for the duration of the request.  Having more persistent user-uploaded tables, however, has quite a few interesting applications.

Inspired by Pat Dowler's 2018 Interop talk on youcat, 
https://wiki.ivoa.net/internal/IVOA/InterOpNov2018DAL/tap-youcat.pdf, I have made a simple implementations for persistent tables in DaCHS.  This notebook shows how this can be operated even without support for it in pyVO.

**Note:** This is certainly not what will eventually become a standard.  Do not do large implementations against what is discussed here.

In [1]:
import pyvo
import requests
# get a table to upload; this must be a VOTable
to_upload = requests.get("https://docs.g-vo.org/upload_for_regressiontest.vot")

In [2]:
GAVO_TAP = "http://dc.g-vo.org/tap"
svc = pyvo.dal.TAPService(GAVO_TAP)

(If it bothers you, feel free to change the URL schema to https; but with http, you can watch what happens with ngrep, wireshark and its ilk without having to jump through too many hoops).

First, we need a VOTable to upload; let me pull one from the net.  The actual upload is a PUT request to a child of a *sibling* of VOSI tables; in the current implementation, that's `user_tables`.  The child name becomes the table name.

In [3]:
res = requests.put(svc.baseurl+"/user_tables/my_upload", 
             data=to_upload.content,
             headers={"content-type": "application/x-votable+xml"})
(res.status_code, res.text)

(200, 'Query this table as tap_user.my_upload')

For now, this returns an explanatory string.  I *think* I will change this with a redirect to the uploaded table's GET URL.  That returns a VOSI tableset (non-nerd speak: column metadata for the uploaded table).  Just use the URI you uploaded to, but do a GET instead of a PUT.  The scary bits are what is required to make pyVO parse this:

In [4]:
import io
from pyvo.io import vosi

def parse_vosi_table(source_data):
    return vosi.parse_tables(io.BytesIO(source_data)).get_first_table()

table_meta = parse_vosi_table(
    requests.get(svc.baseurl+"/user_tables/my_upload").content)
print([c.name for c in table_meta.columns])
print(table_meta.columns[0]. name, table_meta.columns[0].unit)

['"_r"', '"_Glon"', '"_Glat"', '"_RAJ2000"', '"_DEJ2000"', 'c', 'glimpse', '"2MASS"', 'raj2000', 'dej2000', 'jmag', 'hmag', 'kmag', '"3.6mag"', '"e_3.6mag"', '"4.5mag"', '"e_4.5mag"', '"5.8mag"', '"e_5.8mag"', '"8.0mag"', '"e_8.0mag"']
"_r" arcmin


The main point of the exercise is that you can now run TAP queries against your table.  The user-uploaded tables are in the `tap_user` schema.

In [5]:
svc.run_sync("SELECT raj2000, dej2000, jmag FROM tap_user.my_upload"
             " WHERE jmag>10")

<DALResultsTable length=1>
 RAJ2000    DEJ2000     Jmag 
   deg        deg       mag  
 float64    float64   float32
---------- ---------- -------
274.462917 -15.902246  15.821

This (ought to) work just like any other table.  For instance, you can run joins and all that:

In [6]:
svc.run_sync("SELECT source_id FROM gaia.dr3lite JOIN tap_user.my_upload"
             " on (distance(ra, dec, raj2000, dej2000)<0.01)")

<DALResultsTable length=558>
     source_id     
       int64       
-------------------
4098069231903243008
4098069231908985344
4098069231907166464
4098069231903952512
4098069227601633920
4098069266266084864
                ...
4098069266262980352
4098069266272884992
4098069330680796928
4098069266262985472
4098069365040373888
4098069433759852288
4098069266263690624

When done with the uploaded table, you should clean up after yourself by DELETE-ing the table URL:

In [7]:
requests.delete(svc.baseurl+"/user_tables/my_upload").text

'Dropped user table my_upload'

It is not an error to delete a (hopefully) non-existing table:

In [18]:
requests.delete(svc.baseurl+"/user_tables/smallgaia").text

'Dropped user table smallgaia'

As you can see, as with PUT, this returns a little informative plain text string.  I am not really sure where this would redirect to instead.  Perhaps the table listing?  See below, though.

Once that's done (or after some time, in the case of this service seven days), the table is gone from the TAP service:

In [8]:
try:
    svc.run_sync("SELECT COUNT(*) FROM tap_user.my_upload")
except pyvo.DALQueryError as exc:
    print(exc)

Field query: Could not locate table 'tap_user.my_upload'


So, you wonder: Can anyone delete and query my tables?  Well, sort of, as long as you are anonymous – although they would have to guess your table name, and choosing an obvious table name is probably a bad idea because if it is obvious to some other person, too, and then you will overwrite each other's tables even if both of you are benevolent.  

Anyway, once you are authenticated, all these problems go away and you have a `tap_user` all for yourself.  Regrettably, there still is no federated authentication in astronomy, so you will in general have to obtain credentials per service.  For the service we run here, contact gavo@ari.uni-heidelberg.de for credentials.  Or use uptest/uptest – which of course you share with everyone reading this.

In [9]:
session = pyvo.auth.AuthSession()
session.credentials.set_password("uptest", "uptest")
session.add_security_method_for_url(GAVO_TAP, "ivo://ivoa.net/sso#BasicAA")
auth_svc = pyvo.dal.TAPService(GAVO_TAP, session=session)

You can now do the table management as above, except you need to repeat the credentials in the requests call:

In [10]:
requests.put(svc.baseurl+"/user_tables/my_upload", 
             data=to_upload.content,
             auth=("uptest", "uptest"),
             headers={"content-type": "application/x-votable+xml"}).text

'Query this table as tap_user.my_upload'

An alternative way to create persistent tables (that also works for anonymous users) is through `CREATE TABLE`.  This would look like this:

In [21]:
resp = auth_svc.run_sync("CREATE TABLE tap_user.smallgaia AS SELECT *"
                    " FROM gaia.dr3lite TABLESAMPLE(0.001)")

This returns an empty VOTable with the columns metadata of your new table.

In [22]:
resp

<DALResultsTable length=0>
source_id    ra     dec   ... astrometric_params_solved random_index   ruwe 
            deg     deg   ...                                               
  int64   float64 float64 ...           int16              int64     float32
--------- ------- ------- ... ------------------------- ------------ -------

What you cannot do as anonymous: List the tables in your TAP uploads.  You to that by a GET against `user_tables`, and again you get back VOSI tables material:

In [23]:
my_tables = vosi.parse_tables(io.BytesIO(
    requests.get(svc.baseurl+"/user_tables",
    auth=("uptest", "uptest")).content))

In particular, you now see the two tables you uploaded and can inspect their metadata:

In [24]:
table_meta = list(my_tables.iter_tables())
print([t.name for t in table_meta])
print([(c.name, c.unit) for c in table_meta[0].columns])

['tap_user.smallgaia', 'tap_user.my_upload']
[('source_id', None), ('ra', 'deg'), ('dec', 'deg'), ('ra_error', 'mas'), ('dec_error', 'mas'), ('pmra', 'mas/yr'), ('pmdec', 'mas/yr'), ('pmra_error', 'mas/yr'), ('pmdec_error', 'mas/yr'), ('parallax', 'mas'), ('parallax_error', 'mas'), ('phot_g_mean_mag', 'mag'), ('phot_g_mean_flux_over_error', None), ('phot_rp_mean_flux_over_error', None), ('phot_rp_mean_mag', 'mag'), ('phot_bp_mean_flux_over_error', None), ('phot_bp_mean_mag', 'mag'), ('phot_bp_rp_excess_factor', None), ('astrometric_excess_noise', 'mas'), ('radial_velocity', 'km/s'), ('radial_velocity_error', 'km/s'), ('pseudocolour', 'um**-1'), ('pseudocolour_error', 'um**-1'), ('visibility_periods_used', None), ('astrometric_params_solved', None), ('random_index', None), ('ruwe', None)]


Again, you can work table just as you would work with a built-in table.

In [25]:
auth_svc.run_sync(
    "select avg(phot_bp_mean_mag-phot_rp_mean_mag) as avgcolor"
    " from tap_user.smallgaia"
    " where radial_velocity<20").to_table()

<Table length=1>
     avgcolor     
       mag        
     float64      
------------------
1.5359263264614602

An anonymous user cannot see your table (or if they see a tap_user.smallgaia, it's something a joker has created to confuse people trying out this notebook).

In [27]:
try:
    svc.run_sync(
        "select avg(phot_bp_mean_mag-phot_rp_mean_mag)"
        " from tap_user.smallgaia"
        " where radial_velocity<20").to_table()
except Exception as exc:
    print(exc)

Field query: Could not locate table 'tap_user.smallgaia'


Read more on this (or find updated versions of this) on the GAVO blog: http://blog.g-vo.org/a-proposal-for-persistent-tap-uploads.html